In [1]:
# ====================
# 📦 IMPORTS
# ====================
import pandas as pd
import numpy as np
import re
import string
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense, Dropout, Concatenate
from tensorflow.keras.callbacks import EarlyStopping
from sentence_transformers import SentenceTransformer
from sklearn.feature_extraction.text import ENGLISH_STOP_WORDS
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
from transformers import pipeline,AutoTokenizer
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import torch
device = "cuda" if torch.cuda.is_available() else "cpu"

2025-04-05 05:09:28.418875: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2025-04-05 05:09:28.459747: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2025-04-05 05:09:28.461633: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-04-05 05:09:36.084576: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
/users/5/thono001/ondemand/Hackthon/myenv/lib/python3.8/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook imp

In [2]:
#!pip install vaderSentiment

In [3]:
data = pd.read_excel("Training.xlsx")

test_data = pd.read_excel("Test_Truncated.xlsx")

In [4]:
test_data.head()

Match ID 18Char Completion Date  \
0  a1v2J0000027CXKQA2      2017-12-20   
1  a1v2J0000027CXKQA2      2018-01-19   
2  a1v2J0000027CXKQA2      2018-02-18   
3  a1v2J0000027JFCQA2      2018-12-05   
4  a1v2J0000027JFCQA2      2019-02-14   

                         Match Support Contact Notes           Little ID  \
0  Question: Activities:           Answer: BB and...  0032J00003PfqfqQAB   
1  Question: Activities:           Answer: BB and...  0032J00003PfqfqQAB   
2                                                NaN  0032J00003PfqfqQAB   
3  Question: Activities:           Answer: MEC me...  0032J00003PfqfDQAR   
4  Question: Activities:           Answer: MEC sp...  0032J00003PfqfDQAR   

            Big ID Big County  Big Age        Big Occupation Big: Military  \
0  0032J00003Pgbpe     Ramsey       25  Student: High School           NaN   
1  0032J00003Pgbpe     Ramsey       25  Student: High School           NaN   
2  0032J00003Pgbpe     Ramsey       25  Student: High School           NaN   
3  0032J00003PhOyf     Dakota       38        Tech: Engineer           NaN   
4  0032J00003PhOyf     Dakota       38        Tech: Engineer           NaN   

  Big Approved Date  ... Little Other Interests  \
0        2017-12-04  ...                    NaN   
1        2017-12-04  ...                    NaN   
2        2017-12-04  ...                    NaN   
3        2018-11-07  ...                    NaN   
4        2018-11-07  ...                    NaN   

  Little Contact: Interest Finder - Career  \
0                                      NaN   
1                                      NaN   
2                                      NaN   
3                                      NaN   
4                                      NaN   

  Little Contact: Interest Finder - Personality  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3                                           NaN   
4                                           NaN   

  Little Contact: Interest Finder - Three Wishes Little Gender  \
0                                            NaN          Male   
1                                            NaN          Male   
2                                            NaN          Male   
3                                            NaN          Male   
4                                            NaN          Male   

  Little Participant: Race/Ethnicity Little Birthdate  \
0                              Asian       2006-11-01   
1                              Asian       2006-11-01   
2                              Asian       2006-11-01   
3          Black or African American       2006-09-01   
4          Black or African American       2006-09-01   

  Little Mailing Address Census Block Group Big Home Census Block Group  \
0                                       NaN                         NaN   
1                                       NaN                         NaN   
2                                       NaN                         NaN   
3                              2.705302e+11                2.703706e+11   
4                              2.705302e+11                2.703706e+11   

  Big Employer/School Census Block Group  
0                                    NaN  
1                                    NaN  
2                                    NaN  
3                                    NaN  
4                                    NaN  

[5 rows x 63 columns]

# ====================
# 📂 LOAD & FILTER
# ====================

In [6]:
df = data[data["Stage"] == "Closed"]
df = df[df["Match Length"].notna()]
df["Match Activation Date"] = pd.to_datetime(df["Match Activation Date"])
df["Completion Date"] = pd.to_datetime(df["Completion Date"])
test_data["Completion Date"] = pd.to_datetime(test_data["Completion Date"])
df["Little Birthdate"] = pd.to_datetime(df["Little Birthdate"])
df["Big Birthdate"] = pd.to_datetime(df["Big Birthdate"])
test_data["Little Birthdate"] = pd.to_datetime(test_data["Little Birthdate"])
test_data["Big Birthdate"] = pd.to_datetime(test_data["Big Birthdate"])
df = df.sort_values(["Match ID 18Char", "Completion Date"])
test = test_data.sort_values(["Match ID 18Char", "Completion Date"])
test.head()

Match ID 18Char Completion Date  \
0  a1v2J0000027CXKQA2      2017-12-20   
1  a1v2J0000027CXKQA2      2018-01-19   
2  a1v2J0000027CXKQA2      2018-02-18   
3  a1v2J0000027JFCQA2      2018-12-05   
4  a1v2J0000027JFCQA2      2019-02-14   

                         Match Support Contact Notes           Little ID  \
0  Question: Activities:           Answer: BB and...  0032J00003PfqfqQAB   
1  Question: Activities:           Answer: BB and...  0032J00003PfqfqQAB   
2                                                NaN  0032J00003PfqfqQAB   
3  Question: Activities:           Answer: MEC me...  0032J00003PfqfDQAR   
4  Question: Activities:           Answer: MEC sp...  0032J00003PfqfDQAR   

            Big ID Big County  Big Age        Big Occupation Big: Military  \
0  0032J00003Pgbpe     Ramsey       25  Student: High School           NaN   
1  0032J00003Pgbpe     Ramsey       25  Student: High School           NaN   
2  0032J00003Pgbpe     Ramsey       25  Student: High School           NaN   
3  0032J00003PhOyf     Dakota       38        Tech: Engineer           NaN   
4  0032J00003PhOyf     Dakota       38        Tech: Engineer           NaN   

  Big Approved Date  ... Little Other Interests  \
0        2017-12-04  ...                    NaN   
1        2017-12-04  ...                    NaN   
2        2017-12-04  ...                    NaN   
3        2018-11-07  ...                    NaN   
4        2018-11-07  ...                    NaN   

  Little Contact: Interest Finder - Career  \
0                                      NaN   
1                                      NaN   
2                                      NaN   
3                                      NaN   
4                                      NaN   

  Little Contact: Interest Finder - Personality  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3                                           NaN   
4                                           NaN   

  Little Contact: Interest Finder - Three Wishes Little Gender  \
0                                            NaN          Male   
1                                            NaN          Male   
2                                            NaN          Male   
3                                            NaN          Male   
4                                            NaN          Male   

  Little Participant: Race/Ethnicity Little Birthdate  \
0                              Asian       2006-11-01   
1                              Asian       2006-11-01   
2                              Asian       2006-11-01   
3          Black or African American       2006-09-01   
4          Black or African American       2006-09-01   

  Little Mailing Address Census Block Group Big Home Census Block Group  \
0                                       NaN                         NaN   
1                                       NaN                         NaN   
2                                       NaN                         NaN   
3                              2.705302e+11                2.703706e+11   
4                              2.705302e+11                2.703706e+11   

  Big Employer/School Census Block Group  
0                                    NaN  
1                                    NaN  
2                                    NaN  
3                                    NaN  
4                                    NaN  

[5 rows x 63 columns]

In [7]:
base_columns=['Match ID 18Char', 'Completion Date', 'Match Support Contact Notes','Big Gender','Big Occupation',
       'Big Birthdate', 'Program', 'Program Type',
       'Big Race/Ethnicity', 'Little Gender',
       'Little Participant: Race/Ethnicity', 'Little Birthdate',
       'Match Activation Date','Rationale for Match','Match Length','Closure Reason']

base_columns_test=['Match ID 18Char', 'Completion Date', 'Match Support Contact Notes','Big Gender','Big Occupation',
       'Big Birthdate', 'Program', 'Program Type',
       'Big Race/Ethnicity', 'Little Gender',
       'Little Participant: Race/Ethnicity', 'Little Birthdate',
       'Match Activation Date','Rationale for Match']

df=df[base_columns]

test=test[base_columns_test]
columns_with_nulls = [
    'Completion Date',
    'Closure Reason'
]

# Step 1: Identify match_ids with nulls in any of the specified columns
match_ids_with_any_nulls = df[df[columns_with_nulls].isnull().any(axis=1)]['Match ID 18Char'].unique()

# Step 2: Remove all rows corresponding to those match IDs
df = df[~df['Match ID 18Char'].isin(match_ids_with_any_nulls)]

df.head()

Match ID 18Char Completion Date  \
37584  a1v2J0000027CWYQA2      2017-03-23   
37585  a1v2J0000027CWYQA2      2017-05-11   
37583  a1v2J0000027CWYQA2      2017-07-06   
37586  a1v2J0000027CWYQA2      2017-08-31   
34261  a1v2J0000027CWfQAM      2017-02-08   

                             Match Support Contact Notes Big Gender  \
37584  Question: Activities:           Answer: BS ass...     Female   
37585  Question: Activities:           Answer: When a...     Female   
37583  Question: Activities:           Answer: This m...     Female   
37586                                                NaN     Female   
34261  Question: Activities:           Answer: Sami a...     Female   

             Big Occupation Big Birthdate   Program Program Type  \
37584  Student: High School    1999-10-01  YIP 2016         Site   
37585  Student: High School    1999-10-01  YIP 2016         Site   
37583  Student: High School    1999-10-01  YIP 2016         Site   
37586  Student: High School    1999-10-01  YIP 2016         Site   
34261      Student: College    1998-06-01  YIP 2016         Site   

        Big Race/Ethnicity Little Gender Little Participant: Race/Ethnicity  \
37584               Asian;        Female                              Asian   
37585               Asian;        Female                              Asian   
37583               Asian;        Female                              Asian   
37586               Asian;        Female                              Asian   
34261  White or Caucasian;        Female          Black or African American   

      Little Birthdate Match Activation Date Rationale for Match  \
37584       2005-10-01            2017-03-16                 NaN   
37585       2005-10-01            2017-03-16                 NaN   
37583       2005-10-01            2017-03-16                 NaN   
37586       2005-10-01            2017-03-16                 NaN   
34261       2006-08-01            2017-01-23                 NaN   

       Match Length        Closure Reason  
37584           5.5      Child: Graduated  
37585           5.5      Child: Graduated  
37583           5.5      Child: Graduated  
37586           5.5      Child: Graduated  
34261           8.5  Child: Lost interest

# ====================
# 🧠 STRUCTURED FEATURES
# ====================

In [8]:

df["Big Ethnicity Cleaned"] = df["Big Race/Ethnicity"].fillna("Prefer not to say").str.split(";").str[0]
df["Little Ethnicity Cleaned"] = df["Little Participant: Race/Ethnicity"].fillna("Prefer not to say").str.split(";").str[0]

test["Big Ethnicity Cleaned"] = test["Big Race/Ethnicity"].fillna("Prefer not to say").str.split(";").str[0]
test["Little Ethnicity Cleaned"] = test["Little Participant: Race/Ethnicity"].fillna("Prefer not to say").str.split(";").str[0]


occupation_map = {
      'Student': ['Student'],
      'Healthcare': ['Medical', 'Healthcare', 'Nurse', 'Pharmacist', 'Doctor'],
      'Education': ['Education', 'College Professor', 'Teacher'],
      'Law': ['Law', 'Lawyer', 'Police', 'Paralegal', 'Security Officer'],
      'Tech': ['Tech', 'Engineer', 'Computer', 'Programmer', 'Support'],
      'Finance': ['Finance', 'Economist', 'Banking', 'Auditor', 'Accountant'],
      'Retail': ['Retail', 'Customer Service', 'Sales'],
      'Human Services': ['Human Services', 'Social Worker', 'Psychologist', 'Youth Worker'],
      'Transportation': ['Transport'],
      'Service': ['Service', 'Hotel', 'Restaurant', 'Tourism'],
      'Business': ['Business', 'Mgt', 'Marketing', 'Admin', 'Clerical', 'HR'],
      'Entrepreneur': ['Self-Employed', 'Consultant'],
      'Government': ['Govt'],
      'Other': ['Unemployed', 'Unknown', 'Retired', 'Homemaker', 'nan']
  }
def map_occupation(raw):
    if pd.isna(raw):
        return 'Other'
    for k, values in occupation_map.items():
        if any(v.lower() in raw.lower() for v in values):
            return k
    return 'Other' 

df['Big Occupation'] = df['Big Occupation'].apply(map_occupation)

df["Same Ethnicity"] = (df["Big Ethnicity Cleaned"] == df["Little Ethnicity Cleaned"]).astype(int)
df["Same Gender"] = (df["Big Gender"] == df["Little Gender"]).astype(int)
df["Alignment Count"] = df["Same Gender"] + df["Same Ethnicity"]
df["Has Shared Interests"] = df["Rationale for Match"].str.contains("shared interests", case=False, na=False).astype(int)
df["Little Age at Match"] = df["Match Activation Date"].dt.year - df["Little Birthdate"].dt.year
df["Big Age at Match"] = df["Match Activation Date"].dt.year - df["Big Birthdate"].dt.year
df["Age Difference"] = abs(df["Big Age at Match"] - df["Little Age at Match"])
df["Days Since Last"] = df.groupby("Match ID 18Char")["Completion Date"].diff().dt.days
df["Days Since Last"] = df["Days Since Last"].fillna(0)

In [9]:
test['Big Occupation'] = test['Big Occupation'].apply(map_occupation)

test["Same Ethnicity"] = (test["Big Ethnicity Cleaned"] == test["Little Ethnicity Cleaned"]).astype(int)
test["Same Gender"] = (test["Big Gender"] == test["Little Gender"]).astype(int)
test["Alignment Count"] = test["Same Gender"] + test["Same Ethnicity"]
test["Has Shared Interests"] = test["Rationale for Match"].str.contains("shared interests", case=False, na=False).astype(int)
test["Little Age at Match"] = test["Match Activation Date"].dt.year - test["Little Birthdate"].dt.year
test["Big Age at Match"] = test["Match Activation Date"].dt.year - test["Big Birthdate"].dt.year
test["Age Difference"] = abs(test["Big Age at Match"] - test["Little Age at Match"])
test["Days Since Last"] = test.groupby("Match ID 18Char")["Completion Date"].diff().dt.days
test["Days Since Last"] = test["Days Since Last"].fillna(0)

In [11]:
import pandas as pd
import re

# Function to extract interest-like phrases using regex and split them
def extract_interests_simple(text):
    if not isinstance(text, str) or not text.strip():
        return []

    # Patterns to extract phrases that mention shared interests
    interest_patterns = [
        r"shared interests include (.*?)(\.|\n|They|B_|L_|$)",
        r"share various interests (but mostly|like|including)? (.*?)(\.|\n|They|B_|L_|$)",
        r"both (like|enjoy|love|are interested in|have interest in) (.*?)(\.|\n|They|B_|L_|$)",
        r"Shared Interests: (.*?)(\.|\n|They|B_|L_|$)"
    ]

    matches = []
    for pattern in interest_patterns:
        found = re.findall(pattern, text, flags=re.IGNORECASE)
        for match in found:
            # Handle if it's a tuple (from multiple regex capture groups)
            phrase = match[1] if isinstance(match, tuple) else match
            matches.append(phrase.strip())

    # Combine all found interest phrases
    combined = " | ".join(matches)

    # Split on common delimiters and clean up
    raw_interests = re.split(r',| and |;|/', combined.lower())
    interests = [i.strip() for i in raw_interests if len(i.strip()) > 2]

    return list(set(interests))  # remove duplicates

# Apply the extractor
df['shared_interests'] = df['Rationale for Match'].apply(extract_interests_simple)
df['shared_interest_count'] = df['shared_interests'].apply(len)

test['shared_interests'] = test['Rationale for Match'].apply(extract_interests_simple)
test['shared_interest_count'] = test['shared_interests'].apply(len)

# Preview the result
print(df[['shared_interests', 'shared_interest_count']])


                                    shared_interests  shared_interest_count
37584                                             []                      0
37585                                             []                      0
37583                                             []                      0
37586                                             []                      0
34261                                             []                      0
...                                              ...                    ...
31822                                             []                      0
31821                                             []                      0
31820                                             []                      0
39329                                             []                      0
31304  [crafts, arts, trying new things | ., sports]                      4

[26341 rows x 2 columns]


In [12]:
import re
import pandas as pd

def extract_first_miles(text):
    if not isinstance(text, str):
        return None

    # Step 1: Extract all content inside parentheses
    paren_contents = re.findall(r'\(([^)]*)\)', text)

    # Step 2: Remove all parentheses from the text
    text_no_parens = re.sub(r'\([^)]*\)', ' ', text)

    # Step 3: Combine everything into one search string
    combined_text = (text_no_parens + " " + " ".join(paren_contents)).lower()

    # Step 4: Add a space between non-space and capital letter (to split `)Shared`)
    combined_text = re.sub(r'([a-z\)])([A-Z])', r'\1 \2', combined_text)

    # Step 5: Search for miles or mi
    matches = re.findall(r'\b(\d+(?:\.\d+)?)\s*(mi|miles?)\b', combined_text)

    if matches:
        return float(matches[0][0])  # Get the numeric part
    return None

# Apply to your DataFrame
df['miles_apart'] = df['Rationale for Match'].apply(extract_first_miles)

test['miles_apart'] = test['Rationale for Match'].apply(extract_first_miles)

# Preview the output
print(df[['Rationale for Match', 'miles_apart']].head())


      Rationale for Match  miles_apart
37584                 NaN          NaN
37585                 NaN          NaN
37583                 NaN          NaN
37586                 NaN          NaN
34261                 NaN          NaN


# ====================
# ✍️ CLEAN TEXT & SENTIMENT
# ====================

In [17]:
analyzer = SentimentIntensityAnalyzer()
emotional_model_name = "j-hartmann/emotion-english-distilroberta-base"
emotional_tokenizer = AutoTokenizer.from_pretrained(emotional_model_name)
emotional_model = AutoModelForSequenceClassification.from_pretrained(emotional_model_name).to(device)
id2label = emotional_model.config.id2label

def preprocess_notes(text):
    if pd.isna(text): return ""
    text = text.lower()
    replacements = {
        r"\b(big|bs|bbbs|bb|bfirstname|b_first_name)\b": "mentor",
        r"\b(little|ls|lb|lfirstname|l_first_name)\b": "mentee",
        r"\b(pg)\b": "parent",
        r"\b(mec|mc|mss)\b": "coordinator"
    }
    for pattern, replacement in replacements.items():
        text = re.sub(pattern, replacement, text)
    text = re.sub(r"question:[^:\n]+:\s*answer:", "", text, flags=re.IGNORECASE)
    text = re.sub(r"\bcoordinator\b[^?.;!\n]*\?", "", text)
    for ph in ["email_address", "phone_number"]:
        text = text.replace(ph, "")
    text = text.translate(str.maketrans('', '', string.punctuation))
    text = re.sub(r'\d+', '', text)
    text = re.sub(r"\s+", " ", text).strip()
    return " ".join([w for w in text.split() if w not in ENGLISH_STOP_WORDS])

def preprocess_notes2(text):
    if pd.isna(text): return ""
    text = text.lower()
    
    replacements = {
        r"\b(big|bs|bbbs|bb|bfirstname|b_first_name)\b": "mentor",
        r"\b(little|ls|lb|lfirstname|l_first_name)\b": "mentee",
        r"\b(pg)\b": "parent",
        r"\b(mec|mc|mss)\b": "coordinator"
    }
    for pattern, replacement in replacements.items():
        text = re.sub(pattern, replacement, text)

    # Remove QA labels
    text = re.sub(r"question:[^:\n]+:\s*answer:", "", text, flags=re.IGNORECASE)
    text = re.sub(r"\bcoordinator\b[^?.;!\n]*\?", "", text)

    # Remove placeholder tokens
    for ph in ["email_address", "phone_number"]:
        text = text.replace(ph, "")
    
    # Remove common null indicators like 'na', 'none', etc.
    text = re.sub(r"\b(na|none|null|n/a|x|. . . . . . . .)\b", "", text, flags=re.IGNORECASE)

    # Remove digits
    text = re.sub(r'\d+', '', text)

    # Normalize whitespace
    text = re.sub(r"\s+", " ", text).strip()

    return text

# Load tokenizer and model
tokenizer = AutoTokenizer.from_pretrained("cardiffnlp/twitter-roberta-base-sentiment-latest")
model = AutoModelForSequenceClassification.from_pretrained("cardiffnlp/twitter-roberta-base-sentiment-latest").to(device)

# Labels for the sentiment model
label_map = {0: "negative", 1: "neutral", 2: "positive"}

def compute_sentiments_last_tokens(text, max_length=512):
    if pd.isna(text) or text.strip() == "":
        return np.nan, np.nan, np.nan

    # Tokenize text without truncating yet
    encoded = tokenizer(
        text,
        return_tensors='pt',
        truncation=False,
        padding=False,
        add_special_tokens=True
    )

    input_ids = encoded['input_ids'][0]
    attention_mask = encoded['attention_mask'][0]

    # Truncate from the end to get the last `max_length` tokens
    if input_ids.shape[0] > max_length:
        input_ids = input_ids[-max_length:]
        attention_mask = attention_mask[-max_length:]

    input_ids = input_ids.unsqueeze(0).to(device)
    attention_mask = attention_mask.unsqueeze(0).to(device)

    # Run through model
    with torch.no_grad():
        outputs = model(input_ids=input_ids, attention_mask=attention_mask)
        scores = torch.nn.functional.softmax(outputs.logits, dim=1)[0].cpu().numpy()

    return scores[2], scores[1], scores[0]  # Positive, Neutral, Negative

def get_emotion_scores_batch(texts, batch_size=16):
    all_probs = []
    for i in range(0, len(texts), batch_size):
        batch_texts = texts[i:i+batch_size]

        # Tokenize entire batch at once
        inputs = emotional_tokenizer(batch_texts, return_tensors="pt", truncation=True,
                           max_length=256, padding=True)
        inputs = {k: v.to(device) for k, v in inputs.items()}

        with torch.no_grad():
            outputs = emotional_model(**inputs)
            logits = outputs.logits
            probs = torch.nn.functional.softmax(logits, dim=-1).cpu().numpy()

        # Convert each row in the batch to emotion prob dict
        for row in probs:
            emotion_probs = {}
            for idx, label in id2label.items():
                emotion_probs[label] = float(row[idx])
            all_probs.append(emotion_probs)

    return all_probs


df["cleaned_notes"] = df["Match Support Contact Notes"].apply(preprocess_notes2)
df[['Positive_Sentiment', 'Neutral_Sentiment', 'Negative_Sentiment']] = df['cleaned_notes'].apply(lambda x: pd.Series(compute_sentiments_last_tokens(x)))

test["cleaned_notes"] = test["Match Support Contact Notes"].apply(preprocess_notes2)
test[['Positive_Sentiment', 'Neutral_Sentiment', 'Negative_Sentiment']] = test['cleaned_notes'].apply(lambda x: pd.Series(compute_sentiments_last_tokens(x)))


# Step 1: Run the batch function on your cleaned notes
emotion_scores = get_emotion_scores_batch(df["cleaned_notes"].tolist())

# Step 2: Convert list of dicts into a DataFrame
emotion_df = pd.DataFrame(emotion_scores)

# Step 3: Concatenate with original DataFrame
df = pd.concat([df.reset_index(drop=True), emotion_df.reset_index(drop=True)], axis=1)


# Step 1: Run the batch function on your cleaned notes
emotion_scores = get_emotion_scores_batch(test["cleaned_notes"].tolist())

# Step 2: Convert list of dicts into a DataFrame
emotion_df = pd.DataFrame(emotion_scores)

# Step 3: Concatenate with original DataFrame
test = pd.concat([test.reset_index(drop=True), emotion_df.reset_index(drop=True)], axis=1)

Some weights of the model checkpoint at cardiffnlp/twitter-roberta-base-sentiment-latest were not used when initializing RobertaForSequenceClassification: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [18]:
def generate_full_sample(df, sample_replace):
    df['Completion Date'] = pd.to_datetime(df['Completion Date'])
    unique_match_ids = df['Match ID 18Char'].unique()
    match_id_counts = {}
    new_rows = []

    # Step 1: Always include all unique match IDs once
    sampled_match_ids = list(unique_match_ids)

    # Step 2 (optional): Add more samples with replacement if enabled
    if sample_replace:
        extra_samples = np.random.choice(unique_match_ids, size=len(unique_match_ids), replace=True)
        sampled_match_ids.extend(extra_samples)

    # Step 3: Sample and truncate
    for match_id in sampled_match_ids:
        match_df = df[df['Match ID 18Char'] == match_id].sort_values('Completion Date').copy()

        # Pick random cutoff
        pct = np.random.uniform(0.1, 1)
        cutoff = int(np.ceil(len(match_df) * pct))
        truncated_df = match_df.iloc[:cutoff]

        count = match_id_counts.get(match_id, 0)
        new_match_id = f"{match_id}_copy{count}"
        truncated_df['Real Match 18Char'] = match_id
        truncated_df['Match ID 18Char'] = new_match_id
        truncated_df['Match tag'] = count
        match_id_counts[match_id] = count + 1

        new_rows.append(truncated_df)

    result_df = pd.concat(new_rows).drop_duplicates(subset=['Match ID 18Char', 'Completion Date'])
    return result_df.reset_index(drop=True)

df_sampled=generate_full_sample(df,True)
df_sampled[['Positive_Sentiment', 'Neutral_Sentiment', 'Negative_Sentiment']] = df_sampled[
    ['Positive_Sentiment', 'Neutral_Sentiment', 'Negative_Sentiment']
].fillna(0)


test[['Positive_Sentiment', 'Neutral_Sentiment', 'Negative_Sentiment']] = test[
    ['Positive_Sentiment', 'Neutral_Sentiment', 'Negative_Sentiment']
].fillna(0)

/tmp/ipykernel_1609153/4169996568.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  truncated_df['Real Match 18Char'] = match_id
/tmp/ipykernel_1609153/4169996568.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  truncated_df['Match ID 18Char'] = new_match_id
/tmp/ipykernel_1609153/4169996568.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pyd

In [21]:
from sklearn.linear_model import LinearRegression

def compute_slope_intercept(group, column_name):
    if len(group) == 1:
        return pd.Series({"slope": 0.0})
    
    # Convert datetime to numeric
    X = group["Completion Date"].map(pd.Timestamp.toordinal).values.reshape(-1, 1)
    y = group[column_name].values

    model = LinearRegression()
    model.fit(X, y)

    return pd.Series({"slope": model.coef_[0]})

def sentiment_cadence_analysis(df):
    df_sorted = df.sort_values(by=['Match ID 18Char', 'Completion Date'])

    # Step 1: Avg time between contacts
    cadence_summary = (
        df_sorted.groupby('Match ID 18Char')['Days Since Last']
        .mean()
        .reset_index()
        .rename(columns={'Days Since Last': 'Avg Days Between Contacts'})
    )

    # Step 2: Concatenate last 5 cleaned notes
    df_sorted['cleaned_notes'] = df_sorted['cleaned_notes'].fillna("").astype(str)
    last_notes = (
        df_sorted.groupby('Match ID 18Char').tail(2)
        .groupby('Match ID 18Char')['cleaned_notes']
        .apply(lambda x: ' ||| '.join(x))
        .reset_index()
        .rename(columns={'cleaned_notes': 'Last Clean Notes Combined'})
    )

    # Step 3: Merge cadence and notes
    df = df.merge(cadence_summary, on='Match ID 18Char', how='left')
    df = df.merge(last_notes, on='Match ID 18Char', how='left')

    # Step 4: Meeting range
    date_diff = df.groupby('Match ID 18Char')['Completion Date'].agg(['min', 'max'])
    date_diff['Meeting Range Days'] = (date_diff['max'] - date_diff['min']).dt.days
    df = df.merge(date_diff[['Meeting Range Days']], on='Match ID 18Char', how='left')

    # Step 5: Sentiment/emotion slopes
    sentiment_cols = [
        'Positive_Sentiment', 'Neutral_Sentiment', 'Negative_Sentiment',
        'anger', 'disgust', 'fear', 'joy', 'neutral', 'sadness', 'surprise'
    ]

    for col in sentiment_cols:
        slope_df = (
            df.groupby("Match ID 18Char")
              .apply(lambda group: compute_slope_intercept(group, col))
              .reset_index()
              .rename(columns={'slope': f'{col}_slope'})
        )
        df = df.merge(slope_df, on='Match ID 18Char', how='inner')

    # Step 6: Calculate age of Little at last meeting
    df['Little Birthdate'] = pd.to_datetime(df['Little Birthdate'])
    df['Completion Date'] = pd.to_datetime(df['Completion Date'])
    latest_dates = df.groupby('Match ID 18Char')['Completion Date'].transform('max')
    df['Little Last Meeting Age'] = (latest_dates - df['Little Birthdate']).dt.days // 365
    
    # Step 7: Final cleanup
    df.drop_duplicates(subset=['Match ID 18Char'], inplace=True)
    #df.drop_duplicates(inplace=True)
    
    return df

In [22]:
grouped_df=sentiment_cadence_analysis(df_sampled)

In [23]:
grouped_test=sentiment_cadence_analysis(df_sampled)

In [26]:
grouped_df=grouped_df[['Match ID 18Char', 'Big Gender', 'Big Occupation', 
     'Program Type', 'Big Race/Ethnicity', 'Little Gender',
       'Little Participant: Race/Ethnicity', 
        'Rationale for Match', 'Match Length',
       'Closure Reason', 'Big Ethnicity Cleaned', 'Little Ethnicity Cleaned',
       'Same Ethnicity', 'Same Gender', 'Alignment Count',
       'Has Shared Interests', 'Big Age at Match',
       'Age Difference', 'Real Match 18Char', 'Match tag',
       'Avg Days Between Contacts', 'Last Clean Notes Combined',
       'Meeting Range Days', 'Positive_Sentiment_slope',
       'Neutral_Sentiment_slope', 'Negative_Sentiment_slope', 'anger_slope',
       'disgust_slope', 'fear_slope', 'joy_slope', 'neutral_slope',
       'sadness_slope', 'surprise_slope', 'Little Last Meeting Age','shared_interest_count','miles_apart']]

In [27]:
grouped_test=grouped_test[['Match ID 18Char', 'Big Gender', 'Big Occupation', 
     'Program Type', 'Big Race/Ethnicity', 'Little Gender',
       'Little Participant: Race/Ethnicity', 
        'Rationale for Match', 'Match Length',
       'Closure Reason', 'Big Ethnicity Cleaned', 'Little Ethnicity Cleaned',
       'Same Ethnicity', 'Same Gender', 'Alignment Count',
       'Has Shared Interests', 'Big Age at Match',
       'Age Difference',
       'Avg Days Between Contacts', 'Last Clean Notes Combined',
       'Meeting Range Days', 'Positive_Sentiment_slope',
       'Neutral_Sentiment_slope', 'Negative_Sentiment_slope', 'anger_slope',
       'disgust_slope', 'fear_slope', 'joy_slope', 'neutral_slope',
       'sadness_slope', 'surprise_slope', 'Little Last Meeting Age','shared_interest_count','miles_apart']]

In [28]:
def sentiment_analysis(df):

    df[['Positive_Sentiment', 'Neutral_Sentiment', 'Negative_Sentiment']] = df['Last Clean Notes Combined'].apply(lambda x: pd.Series(compute_sentiments_last_tokens(x)))

    # Step 1: Run the batch function on your cleaned notes
    emotion_scores = get_emotion_scores_batch(df["Last Clean Notes Combined"].tolist())

    # Step 2: Convert list of dicts into a DataFrame
    emotion_df = pd.DataFrame(emotion_scores)

    # Step 3: Concatenate with original DataFrame
    df = pd.concat([df.reset_index(drop=True), emotion_df.reset_index(drop=True)], axis=1)

    # Embeddings
    model = SentenceTransformer("all-MiniLM-L6-v2")
    #df['cleaned_note'] = df['Last Clean Notes Combined'].fillna("").astype(str).apply(clean_and_truncate_note)
    df['note_embedding'] = df['Last Clean Notes Combined'].apply(model.encode)
    # Emotional tones

    return df

In [29]:
grouped_df_1=sentiment_analysis(grouped_df)

grouped_df_1_test=sentiment_analysis(grouped_test)

In [30]:
grouped_df_1['miles_apart'] = grouped_df_1['miles_apart'].fillna(grouped_df_1['miles_apart'].mean())
grouped_df_1.isna().sum()
cols_to_impute = ['Positive_Sentiment', 'Neutral_Sentiment', 'Negative_Sentiment']
grouped_df_1[cols_to_impute] = grouped_df_1[cols_to_impute].fillna(0)
cols_to_impute_mode = [
    'Big Race/Ethnicity',
    'Little Gender',
    'Little Participant: Race/Ethnicity'
]

for col in cols_to_impute_mode:
    mode_val = grouped_df_1[col].mode(dropna=True)[0]  # Get most frequent value
    grouped_df_1[col] = grouped_df_1[col].fillna(mode_val)

In [31]:
grouped_df_1_test['miles_apart'] = grouped_df_1_test['miles_apart'].fillna(grouped_df_1_test['miles_apart'].mean())
grouped_df_1_test.isna().sum()
cols_to_impute = ['Positive_Sentiment', 'Neutral_Sentiment', 'Negative_Sentiment']
grouped_df_1_test[cols_to_impute] = grouped_df_1_test[cols_to_impute].fillna(0)
cols_to_impute_mode = [
    'Big Race/Ethnicity',
    'Little Gender',
    'Little Participant: Race/Ethnicity'
]

for col in cols_to_impute_mode:
    mode_val = grouped_df_1[col].mode(dropna=True)[0]  # Get most frequent value
    grouped_df_1_test[col] = grouped_df_1_test[col].fillna(mode_val)

In [32]:
from sklearn.model_selection import train_test_split

def train_test_split_by_real_match(df, test_size=0.2, random_state=42):
    # Step 1: Get unique Real Match IDs
    unique_match_ids = df['Real Match 18Char'].unique()

    # Step 2: Train-test split at the Real Match ID level
    train_ids, test_ids = train_test_split(
        unique_match_ids, test_size=test_size, random_state=random_state
    )

    # Step 3: Build the train set — all rows from selected Real Match IDs
    train_df = df[df['Real Match 18Char'].isin(train_ids)]

    # Step 4: Build the test set — for each test Real Match ID, sample one Match tag
    test_candidates = df[df['Real Match 18Char'].isin(test_ids)]

    test_sampled = (
        test_candidates
        .groupby('Real Match 18Char')
        .apply(lambda group: group.sample(1, random_state=random_state))
        .reset_index(drop=True)
    )

    return train_df.reset_index(drop=True), test_sampled.reset_index(drop=True)

In [33]:
train_df, test_df = train_test_split_by_real_match(grouped_df_1, test_size=0.2)

In [34]:
# Step 2: Define columns
features = [ 'Big Gender', 'Big Occupation', 'Program Type',
       'Big Race/Ethnicity', 'Little Gender',
       'Little Participant: Race/Ethnicity',
       'Big Ethnicity Cleaned', 'Little Ethnicity Cleaned',
       'Same Ethnicity', 'Same Gender', 'Alignment Count',
       'Has Shared Interests', 'Big Age at Match', 'Age Difference',
       'Avg Days Between Contacts', 'Meeting Range Days',
       'Positive_Sentiment_slope', 'Neutral_Sentiment_slope', 'Negative_Sentiment_slope',
       'anger_slope', 'disgust_slope', 'fear_slope', 'joy_slope', 'neutral_slope',
       'sadness_slope', 'surprise_slope', 'Little Last Meeting Age',
       'Positive_Sentiment', 'Neutral_Sentiment', 'Negative_Sentiment',
       'anger', 'disgust', 'fear', 'joy', 'neutral', 'sadness', 'surprise','shared_interest_count','miles_apart',
       'note_embedding' ]

target = 'Match Length'

# ====================
# Final Model Building
# ====================

In [ ]:
from sklearn.model_selection import RandomizedSearchCV
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import StandardScaler, OneHotEncoder, FunctionTransformer
from sklearn.metrics import mean_squared_error
from xgboost import XGBRegressor
import numpy as np


train_split_df, val_split_df =train_df, test_df

# Step 3: Preprocessing
categorical_features = [f for f in features if train_df[f].dtype == 'object' and f != 'note_embedding']
numerical_features = [f for f in features if f not in categorical_features + ['note_embedding']]

def expand_embeddings(X):
    return np.vstack(X)

embedding_transformer = Pipeline(steps=[
    ('expand', FunctionTransformer(expand_embeddings, validate=False)),
    ('scale', StandardScaler())
])

preprocessor = ColumnTransformer(transformers=[
    ('num', StandardScaler(), numerical_features),
    ('cat', OneHotEncoder(handle_unknown='ignore', sparse_output=False), categorical_features),
    ('emb', embedding_transformer, 'note_embedding')
])

# Step 4: XGBoost pipeline
pipeline = Pipeline(steps=[
    ('preprocessor', preprocessor),
    ('regressor', XGBRegressor(objective='reg:squarederror', random_state=42))
])

# Step 5: Hyperparameter search
param_grid = {
    'regressor__n_estimators': [300, 400, 500],
    'regressor__max_depth': [7, 8, 10, 12],
    'regressor__learning_rate': [0.01, 0.1, 0.2],
    'regressor__subsample': [0.6, 0.8, 1.0],
    'regressor__colsample_bytree': [0.6, 0.8, 1.0]  # ✅ valid values
}

search = RandomizedSearchCV(
    pipeline,
    param_distributions=param_grid,
    n_iter=15,
    scoring='neg_root_mean_squared_error',
    cv=3,
    verbose=2,
    n_jobs=-1,
    random_state=42
)

# Step 6: Train and evaluate
X_train = train_split_df[features]
y_train = train_split_df[target]
X_val = val_split_df[features]
y_val = val_split_df[target]

search.fit(X_train, y_train)

# Step 7: Evaluate best model
best_model = search.best_estimator_
y_pred = best_model.predict(X_val)
rmse = mean_squared_error(y_val, y_pred, squared=False)

print(f"✅ Best RMSE on custom-validation split: {rmse:.2f}")
print("🔧 Best Hyperparameters:", search.best_params_)

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


Fitting 3 folds for each of 15 candidates, totalling 45 fits


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

[CV] END regressor__colsample_bytree=0.8, regressor__learning_rate=0.2, regressor__max_depth=7, regressor__n_estimators=300, regressor__subsample=0.6; total time= 1.7min
[CV] END regressor__colsample_bytree=0.8, regressor__learning_rate=0.01, regressor__max_depth=10, regressor__n_estimators=300, regressor__subsample=0.6; total time= 6.5min
[CV] END regressor__colsample_bytree=1.0, regressor__learning_rate=0.1, regressor__max_depth=8, regressor__n_estimators=400, regressor__subsample=1.0; total time= 5.4min
[CV] END regressor__colsample_bytree=0.8, regressor__learning_rate=0.1, regressor__max_depth=12, regressor__n_estimators=500, regressor__subsample=1.0; total time= 8.8min
[CV] END regressor__colsample_bytree=0.8, regressor__learning_rate=0.01, regressor__max_depth=10, regressor__n_estimators=500, regressor__subsample=0.6; total time=21.1min
[CV] END regressor__colsample_bytree=0.8, regressor__learning_rate=0.2, regressor__max_depth=7, regressor__n_estimators=500, regressor__subsample

# ====================
# Final Testing
# ====================

In [ ]:


X_test = grouped_df_1_test[features]
X_train = grouped_df_1[features]
y_train = grouped_df_1[target]

best_model.fit(X_train, y_train)
# Predict using the best model
y_test_pred = best_model.predict(X_test)

# ====================
# Other Models Tested
# ====================

In [99]:
from sklearn.ensemble import VotingRegressor
from sklearn.neural_network import MLPRegressor
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import StandardScaler, OneHotEncoder, FunctionTransformer
from sklearn.metrics import mean_squared_error
from xgboost import XGBRegressor
import numpy as np

# Step 1: Preprocessing (reuse your code)
categorical_features = [f for f in features if train_df[f].dtype == 'object' and f != 'note_embedding']
numerical_features = [f for f in features if f not in categorical_features + ['note_embedding']]

def expand_embeddings(X):
    return np.vstack(X)

from sklearn.impute import SimpleImputer

# Step 3: Preprocessing with Imputation
numerical_pipeline = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='mean')),
    ('scaler', StandardScaler())
])

categorical_pipeline = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='most_frequent')),
    ('onehot', OneHotEncoder(handle_unknown='ignore', sparse_output=False))
])

embedding_transformer = Pipeline(steps=[
    ('expand', FunctionTransformer(expand_embeddings, validate=False)),
    ('scale', StandardScaler())
])

preprocessor = ColumnTransformer(transformers=[
    ('num', numerical_pipeline, numerical_features),
    ('cat', categorical_pipeline, categorical_features),
    ('emb', embedding_transformer, 'note_embedding')
])


# Step 2: Define individual models
xgb = XGBRegressor(
    objective='reg:squarederror',
    n_estimators=search.best_params_['regressor__n_estimators'],
    max_depth=search.best_params_['regressor__max_depth'],
    learning_rate=search.best_params_['regressor__learning_rate'],
    subsample=search.best_params_['regressor__subsample'],
    colsample_bytree=search.best_params_['regressor__colsample_bytree'],
    random_state=42
)

mlp = MLPRegressor(
    hidden_layer_sizes=(128, 64),
    activation='relu',
    solver='adam',
    learning_rate_init=0.001,
    max_iter=500,
    random_state=42
)

# Step 3: Wrap both in pipelines with the same preprocessor
xgb_pipe = Pipeline(steps=[
    ('preprocessor', preprocessor),
    ('regressor', xgb)
])

mlp_pipe = Pipeline(steps=[
    ('preprocessor', preprocessor),
    ('regressor', mlp)
])

# Step 4: Create the ensemble using VotingRegressor
ensemble = VotingRegressor(estimators=[
    ('xgb', xgb_pipe),
    ('mlp', mlp_pipe)
])

# Step 5: Fit ensemble model
X_train = train_split_df[features]
y_train = train_split_df[target]
X_val = val_split_df[features]
y_val = val_split_df[target]

ensemble.fit(X_train, y_train)

# Step 6: Evaluate ensemble model
y_pred_ensemble = ensemble.predict(X_val)
rmse_ensemble = mean_squared_error(y_val, y_pred_ensemble, squared=False)

print(f"🤖 Ensemble RMSE on validation split: {rmse_ensemble:.2f}")


🤖 Ensemble RMSE on validation split: 10.91


In [100]:
# Make sure test_df has the same features
X_train = train_df[features]
y_train = train_df[target]
X_test = test_df[features]
y_test = test_df[target]  # Optional — only if you want to compare predictions


ensemble.fit(X_train, y_train)
# Predict using the best model
y_test_pred = ensemble.predict(X_test)

# If actual target is available, calculate RMSE
if target in test_df.columns:
    test_rmse = mean_squared_error(y_test, y_test_pred, squared=False)
    print(f"📊 RMSE on test_df: {test_rmse:.2f}")
else:
    print("✅ Predictions generated for test_df (no actual targets to compare).")

# # Optional: Attach predictions to test_df
# test_df['Predicted_Match_Length'] = y_test_pred

# # Preview the results
# print(test_df[['Real Match 18Char', 'Predicted_Match_Length']].head())

📊 RMSE on test_df: 10.53


#### Light GBM 

In [ ]:
from sklearn.model_selection import RandomizedSearchCV
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import StandardScaler, OneHotEncoder, FunctionTransformer
from sklearn.metrics import mean_squared_error
from lightgbm import LGBMRegressor
import numpy as np
from sklearn.impute import SimpleImputer

# Reuse existing function to split on Real Match ID
def train_test_split_by_real_match(df, test_size=0.2, random_state=42):
    unique_match_ids = df['Real Match 18Char'].unique()
    train_ids, test_ids = train_test_split(unique_match_ids, test_size=test_size, random_state=random_state)
    train_df = df[df['Real Match 18Char'].isin(train_ids)]
    test_candidates = df[df['Real Match 18Char'].isin(test_ids)]
    test_sampled = (
        test_candidates
        .groupby('Real Match 18Char')
        .apply(lambda group: group.sample(1, random_state=random_state))
        .reset_index(drop=True)
    )
    return train_df.reset_index(drop=True), test_sampled.reset_index(drop=True)

# Step 1: Split train_df using custom function
train_split_df, val_split_df = train_test_split_by_real_match(train_df, test_size=0.2)

# Step 2: Define feature types
categorical_features = [f for f in features if train_df[f].dtype == 'object' and f != 'note_embedding']
numerical_features = [f for f in features if f not in categorical_features + ['note_embedding']]

# Step 3: Define preprocessing steps
def expand_embeddings(X):
    return np.vstack(X)

numerical_pipeline = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='mean')),
    ('scaler', StandardScaler())
])

categorical_pipeline = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='most_frequent')),
    ('onehot', OneHotEncoder(handle_unknown='ignore', sparse_output=False))
])

embedding_transformer = Pipeline(steps=[
    ('expand', FunctionTransformer(expand_embeddings, validate=False)),
    ('scale', StandardScaler())
])

preprocessor = ColumnTransformer(transformers=[
    ('num', numerical_pipeline, numerical_features),
    ('cat', categorical_pipeline, categorical_features),
    ('emb', embedding_transformer, 'note_embedding')
])

# Step 4: LightGBM pipeline
pipeline = Pipeline(steps=[
    ('preprocessor', preprocessor),
    ('regressor', LGBMRegressor(objective='regression', random_state=42))
])

# Step 5: Hyperparameter search
param_grid = {
    'regressor__n_estimators': [300, 400, 500],
    'regressor__max_depth': [7, 8, 10, 12],
    'regressor__learning_rate': [0.01, 0.1, 0.2],
    'regressor__subsample': [0.6, 0.8, 1.0],
    'regressor__colsample_bytree': [0.6, 0.8, 1.0]
}

search = RandomizedSearchCV(
    pipeline,
    param_distributions=param_grid,
    n_iter=5,  # 👈 reduced from 15
    scoring='neg_root_mean_squared_error',
    cv=3,
    verbose=2,
    n_jobs=-1,
    random_state=42
)

# Step 6: Train and evaluate
X_train = train_split_df[features]
y_train = train_split_df[target]
X_val = val_split_df[features]
y_val = val_split_df[target]

search.fit(X_train, y_train)

# Step 7: Evaluate best model
best_model = search.best_estimator_
y_pred = best_model.predict(X_val)
rmse = mean_squared_error(y_val, y_pred, squared=False)

print(f"✅ Best RMSE on custom-validation split (LightGBM): {rmse:.2f}")
print("🔧 Best Hyperparameters:", search.best_params_)


Fitting 3 folds for each of 15 candidates, totalling 45 fits


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

In [ ]:
# Make sure test_df has the same features
X_test = test_df[features]
y_test = test_df[target]  # Optional — only if you want to compare predictions
X_train = train_df[features]
y_train = train_df[target]

best_model.fit(X_train, y_train)
# Predict using the best model
y_test_pred = best_model.predict(X_test)

# If actual target is available, calculate RMSE
if target in test_df.columns:
    test_rmse = mean_squared_error(y_test, y_test_pred, squared=False)
    print(f"📊 RMSE on test_df: {test_rmse:.2f}")
else:
    print("✅ Predictions generated for test_df (no actual targets to compare).")

# # Optional: Attach predictions to test_df
# test_df['Predicted_Match_Length'] = y_test_pred

# # Preview the results
# print(test_df[['Real Match 18Char', 'Predicted_Match_Length']].head())

### Neural Network 

In [162]:
# Reuse existing function to split on Real Match ID
def train_test_split_by_real_match(df, test_size=0.2, random_state=42):
    unique_match_ids = df['Real Match 18Char'].unique()
    train_ids, test_ids = train_test_split(unique_match_ids, test_size=test_size, random_state=random_state)
    train_df = df[df['Real Match 18Char'].isin(train_ids)]
    test_candidates = df[df['Real Match 18Char'].isin(test_ids)]
    test_sampled = (
        test_candidates
        .groupby('Real Match 18Char')
        .apply(lambda group: group.sample(1, random_state=random_state))
        .reset_index(drop=True)
    )
    return train_df.reset_index(drop=True), test_sampled.reset_index(drop=True)

In [163]:
# ====================
# 🔐 3-WAY SPLIT
# ====================

train_split_df, test_1 = train_test_split_by_real_match(grouped_df_1, test_size=0.3)
val_split_df, test_split_df = train_test_split(test_1, test_size=0.5)

In [164]:
X_note_train = np.vstack(train_split_df['note_embedding'].values)
X_note_val = np.vstack(val_split_df['note_embedding'].values)
X_note_test=np.vstack(test_split_df['note_embedding'].values)

del train_split_df['note_embedding']
del val_split_df['note_embedding']
del test_split_df['note_embedding']

y_train_split=train_split_df['Match Length'].values
y_test_split=test_split_df['Match Length'].values
y_val_split=val_split_df['Match Length'].values

del train_split_df['Match Length']
del val_split_df['Match Length']
del test_split_df['Match Length']

In [166]:
#train_split_df.isna().sum()

In [168]:
features = features = [ 'Big Gender', 'Big Occupation', 'Program Type',
       'Big Race/Ethnicity', 'Little Gender',
       'Little Participant: Race/Ethnicity',
       'Big Ethnicity Cleaned', 'Little Ethnicity Cleaned',
       'Same Ethnicity', 'Same Gender', 'Alignment Count',
       'Has Shared Interests', 'Big Age at Match', 'Age Difference',
       'Avg Days Between Contacts', 'Meeting Range Days',
       'Positive_Sentiment_slope', 'Neutral_Sentiment_slope', 'Negative_Sentiment_slope',
       'anger_slope', 'disgust_slope', 'fear_slope', 'joy_slope', 'neutral_slope',
       'sadness_slope', 'surprise_slope', 'Little Last Meeting Age',
       'Positive_Sentiment', 'Neutral_Sentiment', 'Negative_Sentiment',
       'anger', 'disgust', 'fear', 'joy', 'neutral', 'sadness', 'surprise','shared_interest_count','miles_apart']

num_cols = ['Same Ethnicity', 'Same Gender', 'Alignment Count',
       'Has Shared Interests', 'Big Age at Match', 'Age Difference',
       'Avg Days Between Contacts', 'Meeting Range Days',
       'Positive_Sentiment_slope', 'Neutral_Sentiment_slope', 'Negative_Sentiment_slope',
       'anger_slope', 'disgust_slope', 'fear_slope', 'joy_slope', 'neutral_slope',
       'sadness_slope', 'surprise_slope', 'Little Last Meeting Age',
       'Positive_Sentiment', 'Neutral_Sentiment', 'Negative_Sentiment',
       'anger', 'disgust', 'fear', 'joy', 'neutral', 'sadness', 'surprise','shared_interest_count','miles_apart']

cat_cols = list(set(train_split_df.columns) - set(num_cols))

preprocessor = ColumnTransformer([
    ("num", StandardScaler(), num_cols),
    ("cat", OneHotEncoder(handle_unknown="ignore"), cat_cols)
])

X_struct_train = preprocessor.fit_transform(train_split_df)
X_struct_val = preprocessor.transform(val_split_df)
X_struct_test = preprocessor.transform(test_split_df)

In [175]:
X_struct_train

<3385x9596 sparse matrix of type '<class 'numpy.float64'>'
	with 152325 stored elements in Compressed Sparse Row format>

In [177]:
# ====================
# 🧠 NEURAL NETWORK REGRESSOR
# ====================
input_struct = Input(shape=(X_struct_train.shape[1],))
s = Dense(512, activation="relu")(input_struct)
s = Dropout(0.4)(s)
s = Dense(256, activation="relu")(s)
s = Dropout(0.3)(s)

input_note = Input(shape=(X_note_train.shape[1],))
n = Dense(512, activation="relu")(input_note)
n = Dropout(0.4)(n)
n = Dense(256, activation="relu")(n)

merged = Concatenate()([s, n])
merged = Dense(256, activation="relu")(merged)
merged = Dropout(0.2)(merged)
out = Dense(1)(merged)

reg_model = Model(inputs=[input_struct, input_note], outputs=out)
reg_model.compile(optimizer="adam", loss="mse", metrics=["RootMeanSquaredError"])

reg_model.fit(
    [X_struct_train, X_note_train], y_train_split,
    validation_data=([X_struct_val, X_note_val], y_val_split),
    epochs=100,
    batch_size=32,
    callbacks=[EarlyStopping(patience=10, restore_best_weights=True)],
    verbose=1
)

Epoch 1/100
106/106 [==============================] - 4s 28ms/step - loss: 218.0496 - root_mean_squared_error: 14.7665 - val_loss: 98.1967 - val_root_mean_squared_error: 9.9094
Epoch 2/100
106/106 [==============================] - 3s 29ms/step - loss: 81.0806 - root_mean_squared_error: 9.0045 - val_loss: 90.2919 - val_root_mean_squared_error: 9.5022
Epoch 3/100
106/106 [==============================] - 3s 28ms/step - loss: 38.3629 - root_mean_squared_error: 6.1938 - val_loss: 97.1690 - val_root_mean_squared_error: 9.8574
Epoch 4/100
106/106 [==============================] - 3s 28ms/step - loss: 24.5932 - root_mean_squared_error: 4.9592 - val_loss: 95.7186 - val_root_mean_squared_error: 9.7836
Epoch 5/100
106/106 [==============================] - 3s 27ms/step - loss: 18.7715 - root_mean_squared_error: 4.3326 - val_loss: 98.2202 - val_root_mean_squared_error: 9.9106
Epoch 6/100
106/106 [==============================] - 3s 28ms/step - loss: 17.4152 - root_mean_squared_error: 4.1732 

In [178]:
# Predict on test set
y_test = y_test_split
y_pred = reg_model.predict([X_struct_test, X_note_test])

# RMSE
import numpy as np
rmse = np.sqrt(np.mean((y_test - y_pred.flatten())**2))
print("✅ Final Holdout Test RMSE (Bayesian Tuned Model):", rmse)

12/12 [==============================] - 0s 2ms/step
✅ Final Holdout Test RMSE (Bayesian Tuned Model): 10.62125358138936


In [185]:
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Dense, Dropout, Input, Concatenate
from tensorflow.keras.optimizers import Adam
from keras_tuner import HyperModel

class MultiInputRegressor(HyperModel):
    def __init__(self, input_struct_dim, input_note_dim):
        self.input_struct_dim = input_struct_dim
        self.input_note_dim = input_note_dim

    def build(self, hp):
        # Structural input
        input_struct = Input(shape=(self.input_struct_dim,))
        s = Dense(hp.Int("struct_units1", 128, 512, step=64), activation="relu")(input_struct)
        s = Dropout(hp.Float("struct_dropout1", 0.2, 0.5, step=0.1))(s)
        s = Dense(hp.Int("struct_units2", 64, 256, step=64), activation="relu")(s)
        s = Dropout(hp.Float("struct_dropout2", 0.1, 0.4, step=0.1))(s)

        # Note embedding input
        input_note = Input(shape=(self.input_note_dim,))
        n = Dense(hp.Int("note_units1", 128, 512, step=64), activation="relu")(input_note)
        n = Dropout(hp.Float("note_dropout1", 0.2, 0.5, step=0.1))(n)
        n = Dense(hp.Int("note_units2", 64, 256, step=64), activation="relu")(n)

        # Merge branches
        merged = Concatenate()([s, n])
        merged = Dense(hp.Int("merged_units", 128, 512, step=64), activation="relu")(merged)
        merged = Dropout(hp.Float("merged_dropout", 0.1, 0.3, step=0.1))(merged)
        out = Dense(1)(merged)

        model = Model(inputs=[input_struct, input_note], outputs=out)

        model.compile(
            optimizer=Adam(learning_rate=hp.Float("lr", 1e-4, 1e-2, sampling="log")),
            loss="mse",
            metrics=["RootMeanSquaredError"]
        )
        return model
    
# Initialize model
hypermodel = MultiInputRegressor(X_struct_train.shape[1], X_note_train.shape[1])

tuner = RandomSearch(
    hypermodel,
    objective=Objective("val_root_mean_squared_error", direction="min"),  # ✅ Fix here
    max_trials=20,
    executions_per_trial=1,
    directory="nn_tuning_dir",
    project_name="multi_input_regression",
    overwrite=True
)

In [186]:
tuner.search(
    [X_struct_train, X_note_train],
    y_train_split,
    validation_data=([X_struct_val, X_note_val], y_val_split),
    epochs=100,
    callbacks=[EarlyStopping(patience=10, restore_best_weights=True)],
    verbose=1
)

Trial 20 Complete [00h 00m 36s]
val_root_mean_squared_error: 9.518905639648438

Best val_root_mean_squared_error So Far: 9.166590690612793
Total elapsed time: 00h 10m 24s


In [187]:
best_model = tuner.get_best_models(num_models=1)[0]


In [188]:
# Predict on test set
y_test_pred = best_model.predict([X_struct_test, X_note_test])

# Optional: evaluate RMSE if true values exist
from sklearn.metrics import mean_squared_error

if y_test is not None:
    test_rmse = mean_squared_error(y_test, y_test_pred, squared=False)
    print(f"📊 Test RMSE from best model: {test_rmse:.2f}")
else:
    print("✅ Predictions generated. No actual labels to compare.")


12/12 [==============================] - 0s 2ms/step
📊 Test RMSE from best model: 10.55


In [184]:
from keras_tuner.tuners import RandomSearch
from keras_tuner import Objective
from tensorflow.keras.callbacks import EarlyStopping





In [ ]:
best_model = tuner.get_best_models(1)[0]
best_hps = tuner.get_best_hyperparameters(1)[0]

print("✅ Best model summary:")
best_model.summary()

print("\n🏆 Best hyperparameters:")
for name, value in best_hps.values.items():
    print(f"{name}: {value}")

In [104]:
# Make sure test_df has the same features
# Reuse existing function to split on Real Match ID
def generate_test(df, test_size=0.2, random_state=42):
    test_ids =df['Real Match 18Char'].unique()
    test_candidates = df[df['Real Match 18Char'].isin(test_ids)]
    test_sampled = (
        test_candidates
        .groupby('Real Match 18Char')
        .apply(lambda group: group.sample(1, random_state=random_state))
        .reset_index(drop=True)
    )
    return test_sampled.reset_index(drop=True)

test_df_sampled=generate_test(test_df)

X_test = test_df_sampled[features]
y_test = test_df_sampled[target]  # Optional — only if you want to compare predictions
X_train = train_df[features]
y_train = train_df[target]

best_model.fit(X_train, y_train)
# Predict using the best model
y_test_pred = best_model.predict(X_test)

# If actual target is available, calculate RMSE
if target in test_df.columns:
    test_rmse = mean_squared_error(y_test, y_test_pred, squared=False)
    print(f"📊 RMSE on test_df: {test_rmse:.2f}")
else:
    print("✅ Predictions generated for test_df (no actual targets to compare).")

# # Optional: Attach predictions to test_df
# test_df['Predicted_Match_Length'] = y_test_pred

# # Preview the results
# print(test_df[['Real Match 18Char', 'Predicted_Match_Length']].head())

📊 RMSE on test_df: 11.84


In [ ]:
import numpy as np
from xgboost import XGBRegressor
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error
from tensorflow.keras.layers import Input, Dense, Dropout, Concatenate
from tensorflow.keras.models import Model
from tensorflow.keras.callbacks import EarlyStopping

# ====================
# 🧠 NEURAL NETWORK REGRESSOR
# ====================
input_struct = Input(shape=(X_struct_train.shape[1],))
s = Dense(512, activation="relu")(input_struct)
s = Dropout(0.4)(s)
s = Dense(256, activation="relu")(s)
s = Dropout(0.3)(s)

input_note = Input(shape=(X_note_train.shape[1],))
n = Dense(512, activation="relu")(input_note)
n = Dropout(0.4)(n)
n = Dense(256, activation="relu")(n)

input_rat = Input(shape=(X_rat_train.shape[1],))
r = Dense(512, activation="relu")(input_rat)
r = Dropout(0.4)(r)
r = Dense(256, activation="relu")(r)

merged = Concatenate()([s, n, r])
merged = Dense(256, activation="relu")(merged)
merged = Dropout(0.2)(merged)
out = Dense(1)(merged)

reg_model = Model(inputs=[input_struct, input_note, input_rat], outputs=out)
reg_model.compile(optimizer="adam", loss="mse", metrics=["RootMeanSquaredError"])

# Train the neural network
reg_model.fit(
    [X_struct_train, X_note_train, X_rat_train], train_df["Match Length"].values,
    validation_data=([X_struct_val, X_note_val, X_rat_val], val_df["Match Length"].values),
    epochs=100,
    batch_size=32,
    callbacks=[EarlyStopping(patience=10, restore_best_weights=True)],
    verbose=1
)

# ====================
# ENSEMBLE WITH XGBOOST AND STACKING
# ====================

# 1. Prepare XGBoost training data by concatenating the three feature sets.
X_xgb_train = np.concatenate([X_struct_train, X_note_train, X_rat_train], axis=1)
X_xgb_val   = np.concatenate([X_struct_val, X_note_val, X_rat_val], axis=1)

# 2. Train the XGBoost model on the combined features.
model_xgb = XGBRegressor(
    n_estimators=1000,
    learning_rate=0.01,
    max_depth=6,
    objective='reg:squarederror',
    verbosity=0
)

model_xgb.fit(
    X_xgb_train, train_df["Match Length"].values,
    early_stopping_rounds=50,
    eval_set=[(X_xgb_train, train_df["Match Length"].values)],
    verbose=False
)

# 3. Generate predictions on the training set from both models.
pred_nn_train = reg_model.predict([X_struct_train, X_note_train, X_rat_train]).flatten()
pred_xgb_train = model_xgb.predict(X_xgb_train).flatten()

# 4. Stack these predictions as new features for the meta-model.
stacked_train = np.column_stack((pred_nn_train, pred_xgb_train))

# 5. Train a meta-model (here, linear regression) to learn the best combination.
meta_model = LinearRegression()
meta_model.fit(stacked_train, train_df["Match Length"].values)

# 6. Generate predictions on the validation set from both models.
pred_nn_val = reg_model.predict([X_struct_val, X_note_val, X_rat_val]).flatten()
pred_xgb_val = model_xgb.predict(X_xgb_val).flatten()
stacked_val = np.column_stack((pred_nn_val, pred_xgb_val))

# 7. Use the meta-model to produce the final ensemble predictions.
ensemble_predictions = meta_model.predict(stacked_val)

# 8. Evaluate the ensemble model using RMSE.
rmse = np.sqrt(mean_squared_error(val_df["Match Length"].values, ensemble_predictions))
print("Ensembled Model RMSE on Validation Set:", rmse)

In [ ]:
pip install matplotlib

In [ ]:
xgb_model = search.best_estimator_.named_steps['regressor']
# Get column transformer
preprocessor = search.best_estimator_.named_steps['preprocessor']

# Get one-hot encoded feature names
cat_features = preprocessor.named_transformers_['cat'].get_feature_names_out(categorical_features)

# All numeric + embedded names
num_features = numerical_features
emb_features = [f"embedding_{i}" for i in range(xgb_model.n_features_in_ - (len(cat_features) + len(num_features)))]

# Combine in correct order
feature_names = list(num_features) + list(cat_features) + emb_features
import matplotlib.pyplot as plt
import xgboost as xgb

# Get importance scores (can use 'weight', 'gain', or 'cover')
importances = xgb_model.feature_importances_

# Create a DataFrame for easy sorting
importance_df = pd.DataFrame({
    'feature': feature_names,
    'importance': importances
}).sort_values(by='importance', ascending=False)

# Plot top 20 features
importance_df.head(50).plot(kind='barh', x='feature', y='importance', figsize=(10, 8), legend=False)
plt.gca().invert_yaxis()
plt.title("Top 20 Feature Importances (XGBoost)")
plt.xlabel("Importance Score")
plt.show()

In [ ]:
#!pip install scikeras

In [ ]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout
from tensorflow.keras.wrappers.scikit_learn import KerasRegressor
from tensorflow.keras.optimizers import Adam
import tensorflow as tf

In [ ]:
def build_model(input_dim=100, learning_rate=0.001, dropout_rate=0.2, num_units=128):
    model = Sequential()
    model.add(Dense(num_units, input_dim=input_dim, activation='relu'))
    model.add(Dropout(dropout_rate))
    model.add(Dense(num_units // 2, activation='relu'))
    model.add(Dropout(dropout_rate))
    model.add(Dense(1))  # Output layer for regression
    model.compile(loss='mse', optimizer=Adam(learning_rate=learning_rate), metrics=['RootMeanSquaredError'])
    return model

In [ ]:
# Placeholder model for pipeline shape inference (will be rebuilt inside RandomizedSearchCV)
keras_reg = KerasRegressor(build_fn=build_model, input_dim=1, verbose=0)

pipeline = Pipeline(steps=[
    ('preprocessor', preprocessor),
    ('regressor', keras_reg)
])

In [ ]:
param_grid = {
    'regressor__input_dim': [len(numerical_features) + len(categorical_features)*10 + 768],  # adjust embedding size
    'regressor__learning_rate': [0.001, 0.005],
    'regressor__dropout_rate': [0.2, 0.3],
    'regressor__num_units': [64, 128, 256],
    'regressor__epochs': [20],
    'regressor__batch_size': [16, 32]
}

In [ ]:
search = RandomizedSearchCV(
    pipeline,
    param_distributions=param_grid,
    n_iter=10,
    scoring='neg_root_mean_squared_error',
    cv=3,
    verbose=2,
    n_jobs=1,  # ⚠️ Can't use n_jobs > 1 with TensorFlow safely
    random_state=42
)

search.fit(X_train, y_train)

# Evaluate
best_model = search.best_estimator_
y_pred = best_model.predict(X_val)
rmse = mean_squared_error(y_val, y_pred, squared=False)
print(f"✅ Best RMSE on custom-validation split: {rmse:.2f}")